# Strategia in tempo reale: contrarian

Iniziamo con una strategia semplice, la strategia **contrarian**

In [13]:
import pandas as pd
import numpy as np
import time
from datetime import datetime, timedelta
import tpqoa

In [14]:
class Trader(tpqoa.tpqoa):
    
    def __init__(self,config_file, instrument, period, window):
        super().__init__(config_file)
        self.instrument = instrument
        self.period=period
        self.tickData = pd.DataFrame()
        self.rawData = None 
        self.ultimoPeriodo = None 
        
        self.data = None
        ########################## STRATEGY SPECIFIC ATTRIBUTES ##############################
        self.window = window
        
    def getMostRecent(self, days=5): 
        '''questo metodo scarica i dati FINO ad adesso'''
        while True:
            now = datetime.utcnow()
            now = now - timedelta(microseconds = now.microsecond) # pay attention, microseconds and then microsecond (singular!!!)
            yesterday = now - timedelta(days= days) # lo chiamo YESTERDAY, ma è l'inizio del periodo da scaricare
            df = self.get_history(instrument = self.instrument, start = yesterday, end = now,
                        granularity= "S5", price="M", localize=False)["c"].to_frame() 
                        # scarico a 5secondi, il che vuol dire che period non può essere più corto!
            df.rename(columns={"c":self.instrument},inplace=True)
            self.rawData = df.resample(self.period, label="right").last().dropna().iloc[:-1]
            self.ultimoPeriodo = self.rawData.index[-1]
            if pd.to_datetime(datetime.utcnow()).tz_localize("UTC") - self.ultimoPeriodo < pd.to_timedelta(self.period):
                break
            else:
                time.sleep(2)
    
    def on_success(self, time, bid, ask):
#        print(time, bid, ask)
        print(self.ticks, end=" ")
        tickCorrente = pd.to_datetime(time)
        df = pd.DataFrame({self.instrument:(ask+bid)/2}, index=[tickCorrente])
        self.tickData=pd.concat((self.tickData,df),axis=0)
        if tickCorrente - self.ultimoPeriodo > pd.to_timedelta(self.period):
            self.resampleJoin()
            # NEW
            self.defineStrategy()
    
    def resampleJoin(self):
        self.rawData=pd.concat((self.rawData,self.tickData.resample(self.period,label="right").last().ffill().iloc[:-1] ),axis=0)
        self.tickData = self.tickData.iloc[-1:] 
        self.ultimoPeriodo = self.rawData.index[-1] 
        
    def defineStrategy(self):
        df = self.rawData.copy()
        df["logRet"]=np.log(df[self.instrument] / df[self.instrument].shift(1))
        df["posizione"]= - np.sign(df.logRet.rolling(self.window).mean())
        # ogni volta mi ricalcolo logRet e la posizione per TUTTI gli intervalli (candele), cosa che quando l'algoritmo
        # gira per lungo tempo diventa molto inefficiente, basterebbe calcolarlo solo per l'ultimo
        self.data = df.copy()
        

In [15]:
trader = Trader("oandaMY.cfg","EUR_USD","1min", window=1)

In [16]:
print(datetime.utcnow())
trader.getMostRecent()
trader.stream_data(trader.instrument,stop=50)

2021-11-09 16:04:29.637978
1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 

In [17]:
trader.rawData

EUR_USD
2021-10-31 21:01:00+00:00  1.155960
2021-10-31 21:03:00+00:00  1.155950
2021-10-31 21:06:00+00:00  1.156120
2021-10-31 21:07:00+00:00  1.156080
2021-10-31 21:08:00+00:00  1.156050
...                             ...
2021-11-09 16:02:00+00:00  1.158330
2021-11-09 16:03:00+00:00  1.158220
2021-11-09 16:04:00+00:00  1.157890
2021-11-09 16:05:00+00:00  1.158005
2021-11-09 16:06:00+00:00  1.157715

[9457 rows x 1 columns]

In [18]:
trader.data

EUR_USD    logRet  posizione
2021-10-31 21:01:00+00:00  1.155960       NaN        NaN
2021-10-31 21:03:00+00:00  1.155950 -0.000009        1.0
2021-10-31 21:06:00+00:00  1.156120  0.000147       -1.0
2021-10-31 21:07:00+00:00  1.156080 -0.000035        1.0
2021-10-31 21:08:00+00:00  1.156050 -0.000026        1.0
...                             ...       ...        ...
2021-11-09 16:02:00+00:00  1.158330 -0.000199        1.0
2021-11-09 16:03:00+00:00  1.158220 -0.000095        1.0
2021-11-09 16:04:00+00:00  1.157890 -0.000285        1.0
2021-11-09 16:05:00+00:00  1.158005  0.000099       -1.0
2021-11-09 16:06:00+00:00  1.157715 -0.000250        1.0

[9457 rows x 3 columns]

# Come inserire ordini in OANDA

In [27]:
import pandas as pd
import tpqoa
api=tpqoa.tpqoa("oandaMY.cfg")

In [31]:
#api.create_order(instrument = "EUR_USD", units = 100000, sl_distance= 0.1, tp_price=1.18, price=1.13)
api.create_order(instrument = "EUR_USD", units = 100000, sl_distance= 0.1)



 {'id': '199', 'time': '2021-11-09T10:40:34.560373101Z', 'userID': 20327260, 'accountID': '101-012-20327260-001', 'batchID': '198', 'requestID': '60906982907721437', 'type': 'ORDER_FILL', 'orderID': '198', 'instrument': 'EUR_USD', 'units': '100000.0', 'gainQuoteHomeConversionFactor': '0.858339484349', 'lossQuoteHomeConversionFactor': '0.86696601183', 'price': 1.15927, 'fullVWAP': 1.15927, 'fullPrice': {'type': 'PRICE', 'bids': [{'price': 1.15916, 'liquidity': '1000000'}, {'price': 1.15915, 'liquidity': '2000000'}, {'price': 1.15914, 'liquidity': '2000000'}, {'price': 1.15912, 'liquidity': '5000000'}], 'asks': [{'price': 1.15927, 'liquidity': '1000000'}, {'price': 1.15929, 'liquidity': '2000000'}, {'price': 1.1593, 'liquidity': '2000000'}, {'price': 1.15931, 'liquidity': '5000000'}], 'closeoutBid': 1.15912, 'closeoutAsk': 1.15931}, 'reason': 'MARKET_ORDER', 'pl': '0.0', 'financing': '0.0', 'commission': '0.0', 'guaranteedExecutionFee': '0.0', 'accountBalance': '106637.5039', 'tradeOpe

In [32]:
api.get_positions()

[{'instrument': 'EUR_USD',
  'pl': '205.4447',
  'unrealizedPL': '-9.5366',
  'marginUsed': '3330.0',
  'resettablePL': '205.4447',
  'financing': '0.0',
  'commission': '0.0',
  'guaranteedExecutionFees': '0.0',
  'long': {'units': '100000.0',
   'averagePrice': 1.15927,
   'tradeIDs': ['199'],
   'pl': '183.9554',
   'unrealizedPL': '-9.5366',
   'resettablePL': '183.9554',
   'financing': '0.0',
   'guaranteedExecutionFees': '0.0'},
  'short': {'units': '0.0',
   'pl': '21.4893',
   'unrealizedPL': '0.0',
   'resettablePL': '21.4893',
   'financing': '0.0',
   'guaranteedExecutionFees': '0.0'}}]

In [33]:
api.get_transactions(tid = 199-1)

[{'id': '199',
  'time': '2021-11-09T10:40:34.560373101Z',
  'userID': 20327260,
  'accountID': '101-012-20327260-001',
  'batchID': '198',
  'requestID': '60906982907721437',
  'type': 'ORDER_FILL',
  'orderID': '198',
  'instrument': 'EUR_USD',
  'units': '100000.0',
  'gainQuoteHomeConversionFactor': '0.858339484349',
  'lossQuoteHomeConversionFactor': '0.86696601183',
  'price': 1.15927,
  'fullVWAP': 1.15927,
  'fullPrice': {'type': 'PRICE',
   'bids': [{'price': 1.15916, 'liquidity': '1000000'},
    {'price': 1.15915, 'liquidity': '2000000'},
    {'price': 1.15914, 'liquidity': '2000000'},
    {'price': 1.15912, 'liquidity': '5000000'}],
   'asks': [{'price': 1.15927, 'liquidity': '1000000'},
    {'price': 1.15929, 'liquidity': '2000000'},
    {'price': 1.1593, 'liquidity': '2000000'},
    {'price': 1.15931, 'liquidity': '5000000'}],
   'closeoutBid': 1.15912,
   'closeoutAsk': 1.15931},
  'reason': 'MARKET_ORDER',
  'pl': '0.0',
  'financing': '0.0',
  'commission': '0.0',
  'gu

In [34]:
api.print_transactions(tid = 199-1)

 199 | 2021-11-09T10:40:34.56 | EUR_USD | 100000.0 |      0.0


In [35]:
api.create_order(instrument = "EUR_USD", units = -100000)



 {'id': '202', 'time': '2021-11-09T10:40:57.686856848Z', 'userID': 20327260, 'accountID': '101-012-20327260-001', 'batchID': '201', 'requestID': '60906983004214724', 'type': 'ORDER_FILL', 'orderID': '201', 'instrument': 'EUR_USD', 'units': '-100000.0', 'gainQuoteHomeConversionFactor': '0.858295057797', 'lossQuoteHomeConversionFactor': '0.86692113878', 'price': 1.15924, 'fullVWAP': 1.15924, 'fullPrice': {'type': 'PRICE', 'bids': [{'price': 1.15924, 'liquidity': '1000000'}, {'price': 1.15923, 'liquidity': '2000000'}, {'price': 1.15922, 'liquidity': '2000000'}, {'price': 1.1592, 'liquidity': '5000000'}], 'asks': [{'price': 1.15931, 'liquidity': '1000000'}, {'price': 1.15933, 'liquidity': '2000000'}, {'price': 1.15934, 'liquidity': '2000000'}, {'price': 1.15935, 'liquidity': '5000000'}], 'closeoutBid': 1.1592, 'closeoutAsk': 1.15935}, 'reason': 'MARKET_ORDER', 'pl': '-2.6008', 'financing': '0.0', 'commission': '0.0', 'guaranteedExecutionFee': '0.0', 'accountBalance': '106634.9031', 'trad

In [36]:
api.get_positions()

[]

In [37]:
api.get_account_summary()

{'id': '101-012-20327260-001',
 'alias': 'Primary',
 'currency': 'EUR',
 'balance': '106634.9031',
 'createdByUserID': 20327260,
 'createdTime': '2021-08-17T16:18:26.408215007Z',
 'guaranteedStopLossOrderMode': 'ALLOWED',
 'pl': '-3599.4684',
 'resettablePL': '-3599.4684',
 'resettablePLTime': '0',
 'financing': '234.3715',
 'commission': '0.0',
 'guaranteedExecutionFees': '0.0',
 'marginRate': '0.02',
 'openTradeCount': 0,
 'openPositionCount': 0,
 'pendingOrderCount': 0,
 'hedgingEnabled': False,
 'unrealizedPL': '0.0',
 'NAV': '106634.9031',
 'marginUsed': '0.0',
 'marginAvailable': '106634.9031',
 'positionValue': '0.0',
 'marginCloseoutUnrealizedPL': '0.0',
 'marginCloseoutNAV': '106634.9031',
 'marginCloseoutMarginUsed': '0.0',
 'marginCloseoutPercent': '0.0',
 'marginCloseoutPositionValue': '0.0',
 'withdrawalLimit': '106634.9031',
 'marginCallMarginUsed': '0.0',
 'marginCallPercent': '0.0',
 'lastTransactionID': '203'}

In [48]:
# order = api.create_order(instrument = "EUR_USD", units = 100000, sl_distance= 0.1, price=1.15, tp_price=1.18, suppress = True, ret= True) 
order = api.create_order(instrument = "EUR_USD", units = 100000, suppress = True, ret= True) 

In [49]:
order

{'id': '208',
 'time': '2021-11-09T10:43:14.779286507Z',
 'userID': 20327260,
 'accountID': '101-012-20327260-001',
 'batchID': '207',
 'requestID': '60906983578985342',
 'type': 'ORDER_FILL',
 'orderID': '207',
 'instrument': 'EUR_USD',
 'units': '100000.0',
 'gainQuoteHomeConversionFactor': '0.858372804359',
 'lossQuoteHomeConversionFactor': '0.866999666714',
 'price': 1.15921,
 'fullVWAP': 1.15921,
 'fullPrice': {'type': 'PRICE',
  'bids': [{'price': 1.15913, 'liquidity': '1000000'},
   {'price': 1.15912, 'liquidity': '2000000'},
   {'price': 1.15911, 'liquidity': '2000000'},
   {'price': 1.15909, 'liquidity': '5000000'}],
  'asks': [{'price': 1.15921, 'liquidity': '1000000'},
   {'price': 1.15923, 'liquidity': '2000000'},
   {'price': 1.15924, 'liquidity': '2000000'},
   {'price': 1.15925, 'liquidity': '5000000'}],
  'closeoutBid': 1.15909,
  'closeoutAsk': 1.15925},
 'reason': 'MARKET_ORDER',
 'pl': '-5.202',
 'financing': '0.0',
 'commission': '0.0',
 'guaranteedExecutionFee': '0

In [50]:
order["units"]

'100000.0'

In [51]:
order["price"] # valid only if you specify a price in the order or if you do NOT specify TP SL prices

1.15921

In [52]:
order2 = api.create_order(instrument = "EUR_USD", units = -100000, suppress = True, ret= True) 

In [53]:
order2["price"]

1.15916

# Inserire ordini nella classe Trader

In [23]:
class Trader(tpqoa.tpqoa):
    
    def __init__(self,config_file, instrument, period, window, units):
        super().__init__(config_file)
        self.instrument = instrument
        self.period=period
        self.tickData = pd.DataFrame()
        self.rawData = None 
        self.ultimoPeriodo = None 
        self.data = None
        # NEW
        self.units = units
        # queste sono le unità che compriamo/vendiamo ad ogni cambio di posizione. Notare che sarebbe meglio
        # comprare e vendere un quantitativo fisso del NOSTRO DENARO e non di unità dello strumento
        self.posizione = 0
        
        ########################## STRATEGY SPECIFIC ATTRIBUTES ##############################
        self.window = window
        
    def getMostRecent(self, days=5): 
        '''questo metodo scarica i dati FINO ad adesso'''
        while True:
            now = datetime.utcnow()
            now = now - timedelta(microseconds = now.microsecond) # pay attention, microseconds and then microsecond (singular!!!)
            yesterday = now - timedelta(days= days) # lo chiamo YESTERDAY, ma è l'inizio del periodo da scaricare
            df = self.get_history(instrument = self.instrument, start = yesterday, end = now,
                        granularity= "S5", price="M", localize=False)["c"].to_frame() 
                        # scarico a 5secondi, il che vuol dire che period non può essere più corto!
            df.rename(columns={"c":self.instrument},inplace=True)
            self.rawData = df.resample(self.period, label="right").last().dropna().iloc[:-1]
            self.ultimoPeriodo = self.rawData.index[-1].tz_localize("UTC")
            if pd.to_datetime(datetime.utcnow()).tz_localize("UTC") - self.ultimoPeriodo < pd.to_timedelta(self.period):
                break
            else:
                time.sleep(2)
    
    def on_success(self, time, bid, ask):
        print(self.ticks, end=" ")
        tickCorrente = pd.to_datetime(time)
        df = pd.DataFrame({self.instrument:(ask+bid)/2}, index=[tickCorrente])
        self.tickData=pd.concat((self.tickData,df),axis=0)
        if tickCorrente - self.ultimoPeriodo > pd.to_timedelta(self.period):
            self.resampleJoin()
            self.defineStrategy()
            # NEW
            self.executeTrade()
    
    def resampleJoin(self):
        self.rawData=pd.concat((self.rawData,self.tickData.resample(self.period,label="right").last().ffill().iloc[:-1] ),axis=0)
        self.tickData = self.tickData.iloc[-1:] 
        self.ultimoPeriodo = self.rawData.index[-1] 
        
    def defineStrategy(self):
        df = self.rawData.copy()
        df["logRet"]=np.log(df[self.instrument] / df[self.instrument].shift(1))
        df["posizione"]= - np.sign(df.logRet.rolling(self.window).mean())
        # ogni volta mi ricalcolo logRet e la posizione per TUTTI gli intervalli (candele), cosa che quando l'algoritmo
        # gira per lungo tempo diventa molto inefficiente, basterebbe calcolarlo solo per l'ultimo
        self.data = df.copy()
        
    def executeTrade(self):
        if self.data.posizione.iloc[-1] == 1: # andiamo lunghi
            if self.posizione == 0:
                order = self.create_order(instrument = self.instrument, units = self.units, suppress=True, ret = True)
                print("VADO LUNGO",self.units,order["price"])
            elif self.posizione == -1:
                order = self.create_order(instrument = self.instrument, units = 2*self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE CORTA E VADO LUNGO",2*self.units,order["price"])
            self.posizione=1
        elif self.data.posizione.iloc[-1] == -1: # andiamo corti
            if self.posizione == 0:
                order = self.create_order(instrument = self.instrument, units = -self.units, suppress=True, ret = True)
                print("VADO CORTO",-self.units,order["price"])
            elif self.posizione == 1:
                order = self.create_order(instrument = self.instrument, units = -2*self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE LUNGA E VADO CORTO",-2*self.units,order["price"])
            self.posizione=-1
        elif self.data.posizione.iloc[-1] == 0: # andiamo neutri
            if self.posizione == 1:
                order = self.create_order(instrument = self.instrument, units = -self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE LUNGA",-self.units,order["price"])
            elif self.posizione == -1:
                order = self.create_order(instrument = self.instrument, units = self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE CORTA",self.units,order["price"])
            self.posizione=0
        

In [24]:
trader = Trader("oandaMY.cfg","EUR_USD","1min", window=1, units=100000)

In [ ]:
print(datetime.utcnow())
trader.getMostRecent()
trader.stream_data(trader.instrument,stop=100)

2021-11-09 16:20:46.099966
1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 VADO LUNGO 100000 1.15765
16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 